In [1]:
import torch
import torch.nn as nn
device=torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
import scipy.io as scio
import numpy as np
import matplotlib.pyplot as plt
from torchsummary import summary
from visdom import Visdom
import datetime
import os

In [2]:
# 创建文件夹
ckpDir = './/ckp//dcg'
if not os.path.exists(ckpDir):
    os.makedirs(ckpDir)

timeForSave = datetime.datetime.now().strftime('%Y_%m_%d_%H:%M:%S')
print(timeForSave)
vizx = 0
viz = Visdom()
viz1 = Visdom()
viz2 = Visdom()
viz3 = Visdom()
viz4 = Visdom()
viz5 = Visdom()
viz6 = Visdom()
viz7 = Visdom()
viz8 = Visdom()
viz9 = Visdom()
viz10 = Visdom()
viz11 = Visdom()

Setting up a new session...
Setting up a new session...


2021_11_12_12:12:54


Setting up a new session...
Setting up a new session...
Setting up a new session...
Setting up a new session...
Setting up a new session...
Setting up a new session...
Setting up a new session...
Setting up a new session...
Setting up a new session...
Setting up a new session...


In [3]:
# # 潜在张量大小
# latent_size = 64
# # 输出通道数
# n_channel = 1
# # 生成网络隐藏层大小
# n_g_feature = 64

# gnet = nn.Sequential(
#     # 输入大小 = （64，1，1）
#     nn.ConvTranspose2d(latent_size, 4 * n_g_feature, kernel_size=4,
#                        bias=False),
#     nn.BatchNorm2d(4 * n_g_feature),
#     nn.ReLU(),
#     # 大小 = （256，4，4）
#     nn.ConvTranspose2d(4 * n_g_feature, 2 * n_g_feature, kernel_size=4,
#                    stride=2, padding=1, bias=False),
#     nn.BatchNorm2d(2 * n_g_feature),
#     nn.ReLU(),
#     # 大小 = （128，8，8）
#     nn.ConvTranspose2d(2 * n_g_feature, n_g_feature, kernel_size=4,
#                    stride=2, padding=1, bias=False),
#     nn.BatchNorm2d(n_g_feature),
#     nn.ReLU(),
#     # 大小 = （64，16，16）
#     nn.ConvTranspose2d(n_g_feature, n_channel, kernel_size=4,
#                    stride=2, padding=1),
#     nn.Sigmoid(),
#     # 图片大小 = （1,40,10）
# ).to(device)
# print(gnet)
# # 鉴别网络隐藏层大小
# n_d_feature = 64
# dnet = nn.Sequential(
#     # 图片大小 = (3, 32, 32)
#     nn.Conv2d(n_channel, n_d_feature, kernel_size=4,
#               stride=2, padding=1),
#     nn.LeakyReLU(0.2),
#     # 大小 = （64，16，16）
#     nn.Conv2d(n_d_feature, 2 * n_d_feature, kernel_size=4,
#                 stride=2, padding=1, bias=False),
#     nn.BatchNorm2d(2 * n_d_feature),
#     nn.LeakyReLU(0.2),
#     # 大小 = (128, 8, 8)
#     nn.Conv2d(2 * n_d_feature, 4 * n_d_feature, kernel_size=4,
#             stride=2, padding=1, bias=False),
#     nn.BatchNorm2d(4 * n_d_feature),
#     nn.LeakyReLU(0.2),
#     # 大小 = (256, 4, 4)
#     nn.Conv2d(4 * n_d_feature, 1, kernel_size=4),
#     # 对数赔率张量大小 = (1, 1, 1)
# ).to(device)
# print(dnet)

In [2]:
# 潜在张量大小
latent_size = 64
# 输出通道数
n_channel = 1
# 生成网络隐藏层大小
n_g_feature = 64

gnet = nn.Sequential(
    # 输入大小 = （64，1，1）
    nn.ConvTranspose2d(latent_size, 8 * n_g_feature, kernel_size=4,
                       bias=False),
    nn.BatchNorm2d(8 * n_g_feature),
    nn.ReLU(),
    # 大小 = （512，4，4）
    nn.ConvTranspose2d(8 * n_g_feature, 4 * n_g_feature, kernel_size=4,
                   stride=2, padding=1, bias=False),
    nn.BatchNorm2d(4 * n_g_feature),
    nn.ReLU(),
    # 大小 = （256，8，8）
    nn.ConvTranspose2d(4 * n_g_feature, 4 * n_g_feature, kernel_size=3,
                   stride=1, padding=0, bias=False),
    nn.BatchNorm2d(4 * n_g_feature),
    nn.ReLU(),
    # 大小 = （256，10，10）
    nn.ConvTranspose2d(4 * n_g_feature, 2 * n_g_feature, kernel_size=(4,1),
                   stride=(2,1), padding=(1,0), bias=False),
    nn.BatchNorm2d(2 * n_g_feature),
    nn.ReLU(),
    # 大小 = （128，20，10）
    nn.ConvTranspose2d(2 * n_g_feature, 1 * n_g_feature, kernel_size=(4,1),
                   stride=(2,1), padding=(1,0), bias=False),
    nn.BatchNorm2d(n_g_feature),
    nn.ReLU(),    
    # 大小 = （64，40，10）
    
    nn.ConvTranspose2d(n_g_feature, n_channel, kernel_size=1,
                   stride=1, padding=0),
                   
    nn.Sigmoid(),
    # 图片大小 = （1,40,10）
).to(device)
print(gnet)
summary(gnet,(64,1,1),batch_size = 1,device = "cuda")
# 鉴别网络隐藏层大小
n_d_feature = 64
dnet = nn.Sequential(
    # 图片大小 = (1, 40, 10)
    nn.Conv2d(n_channel, n_d_feature, kernel_size=1,
              stride=1, padding=0),
    nn.LeakyReLU(0.2),
    # 大小 = （64，40，10）
    nn.Conv2d(n_d_feature, 2 * n_d_feature, kernel_size=(4,1),
                stride=(2,1), padding=(1,0), bias=False),
    nn.BatchNorm2d(2 * n_d_feature),
    nn.LeakyReLU(0.2),
    # 大小 = (128, 20, 10)
    nn.Conv2d(2 * n_d_feature, 4 * n_d_feature, kernel_size=(3,1),
            stride=(2,1), padding=(1,0), bias=False),
    nn.BatchNorm2d(4 * n_d_feature),
    nn.LeakyReLU(0.2),
    # 大小 = (256, 10, 10)
    nn.Conv2d(4 * n_d_feature, 4 * n_d_feature, kernel_size=3,
            stride=1, padding=0, bias=False),
    nn.BatchNorm2d(4 * n_d_feature),
    nn.LeakyReLU(0.2),
    # 大小 = (256, 8, 8)
    nn.Conv2d(4 * n_d_feature, 8 * n_d_feature, kernel_size=4,
            stride=2, padding=1, bias=False),
    nn.BatchNorm2d(8 * n_d_feature),
    nn.LeakyReLU(0.2),
    # 大小 = (512, 4, 4)

    nn.Conv2d(8 * n_d_feature, 1, kernel_size=4),
    # 对数赔率张量大小 = (1, 1, 1)
).to(device)
print(dnet)
summary(dnet,(1,40,10),batch_size = 1,device = "cuda")

Sequential(
  (0): ConvTranspose2d(64, 512, kernel_size=(4, 4), stride=(1, 1), bias=False)
  (1): BatchNorm2d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (2): ReLU()
  (3): ConvTranspose2d(512, 256, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
  (4): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (5): ReLU()
  (6): ConvTranspose2d(256, 256, kernel_size=(3, 3), stride=(1, 1), bias=False)
  (7): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (8): ReLU()
  (9): ConvTranspose2d(256, 128, kernel_size=(4, 1), stride=(2, 1), padding=(1, 0), bias=False)
  (10): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (11): ReLU()
  (12): ConvTranspose2d(128, 64, kernel_size=(4, 1), stride=(2, 1), padding=(1, 0), bias=False)
  (13): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (14): ReLU()
  (15): ConvTranspose2d(64, 

In [5]:
import torch.nn.init as init

def weights_init(m):
    if type(m) in [nn.ConvTranspose2d, nn.Conv2d]:
        init.xavier_normal_(m.weight)
    elif type(m) == nn.BatchNorm2d:
        init.normal_(m.weight, 1.0, 0.02)
        init.constant_(m.bias, 0)

gnet.apply(weights_init)
dnet.apply(weights_init)

Sequential(
  (0): Conv2d(1, 64, kernel_size=(1, 1), stride=(1, 1))
  (1): LeakyReLU(negative_slope=0.2)
  (2): Conv2d(64, 128, kernel_size=(4, 1), stride=(2, 1), padding=(1, 0), bias=False)
  (3): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (4): LeakyReLU(negative_slope=0.2)
  (5): Conv2d(128, 256, kernel_size=(3, 1), stride=(2, 1), padding=(1, 0), bias=False)
  (6): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (7): LeakyReLU(negative_slope=0.2)
  (8): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), bias=False)
  (9): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (10): LeakyReLU(negative_slope=0.2)
  (11): Conv2d(256, 512, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
  (12): BatchNorm2d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (13): LeakyReLU(negative_slope=0.2)
  (14): Conv2d(512, 1, kernel_size=(4, 4), stride=(1, 1))
)

In [6]:
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms


transform = transforms.Compose([
    transforms.ToTensor(),  # 将图片转换为Tensor,归一化至[0,1]
])

class EMGDataset(Dataset):
 
    def __init__(self, data, label):
        self.data = data
        self.label = label
        self.transforms = transform
 
    def __getitem__(self, index):
        emgData = self.data[index,:,:,:]
        emgData = np.squeeze(emgData)
        emglabel = self.label[index]
        emglabel = emglabel.astype(np.int16)
        emgData = self.transforms(emgData)        
        return emgData,emglabel
 
    def __len__(self):
        return len(self.label)
 
 
# if __name__ == '__main__':
traindata = np.load('../data/trainX.npy')
trainlabel = np.load('../data/trainY.npy')
print(trainlabel[:,0])

trainlabel = trainlabel[:,0]
print(type(trainlabel))
train_set = EMGDataset(traindata, trainlabel)

train_loader = torch.utils.data.DataLoader(train_set, batch_size=1, shuffle=True, pin_memory=True,
                                            num_workers=3)

sample = next(iter(train_set))
print(sample)

[ 0  0  0 ... 51 51 51]
<class 'numpy.ndarray'>
(tensor([[[0.0171, 0.0073, 0.0024, 0.0024, 0.0024, 0.0024, 0.0757, 0.0317,
          0.0024, 0.0146],
         [0.0171, 0.0244, 0.0024, 0.0024, 0.0024, 0.0024, 0.0684, 0.0342,
          0.0024, 0.0146],
         [0.0146, 0.0269, 0.0024, 0.0024, 0.0024, 0.0024, 0.0610, 0.0342,
          0.0024, 0.0146],
         [0.0220, 0.0195, 0.0024, 0.0024, 0.0024, 0.0024, 0.0513, 0.0366,
          0.0024, 0.0098],
         [0.0269, 0.0171, 0.0024, 0.0024, 0.0024, 0.0024, 0.0488, 0.0415,
          0.0024, 0.0073],
         [0.0269, 0.0293, 0.0024, 0.0024, 0.0024, 0.0024, 0.0732, 0.0488,
          0.0024, 0.0073],
         [0.0244, 0.0317, 0.0024, 0.0024, 0.0024, 0.0024, 0.1001, 0.0635,
          0.0024, 0.0098],
         [0.0220, 0.0244, 0.0024, 0.0024, 0.0024, 0.0024, 0.1074, 0.0757,
          0.0024, 0.0195],
         [0.0171, 0.0146, 0.0024, 0.0024, 0.0024, 0.0024, 0.1172, 0.0854,
          0.0024, 0.0220],
         [0.0195, 0.0049, 0.0024, 0.0024, 

In [7]:
from torch.utils.data import DataLoader
from torchvision.datasets import CIFAR10
import torchvision.transforms as transforms
from torchvision.utils import save_image

# dataset = CIFAR10(root = './data', download=True,
#                   transform=transforms.ToTensor())
# dataloader = DataLoader(dataset, batch_size=64, shuffle=True)
train_loader = torch.utils.data.DataLoader(train_set, batch_size=64)

batch = next(iter(train_loader)) # Get Batch
images, labels = batch
images = images.to(torch.float32)
labels = labels.long()

# for batch_idx, data in enumerate(train_loader):
#     # real_images,real_labels = train_set
#     real_images,real_labels = next(iter(train_loader))
#     # batch_size = real_images.size(0)
#     # print('#{} has {} images.'.format(batch_idx, batch_size))
#     if batch_idx % 100 == 0:
#         path = './data/CIFAR10_shuffled_batch{:03d}.png'.format(batch_idx)
#         save_image(real_images, path, normalize=True)

In [11]:
import torch
import torch.optim
import torch.nn.functional as F

# device =  torch.device("cpu")

# 损失
criterion = nn.BCEWithLogitsLoss().to(device)
# criterion = F.cross_entropy()

# 优化器
goptimizer = torch.optim.Adam(gnet.parameters(),
        lr=0.0002, betas=(0.5, 0.999))
doptimizer = torch.optim.Adam(dnet.parameters(),
        lr=0.00000002, betas=(0.5, 0.999))
g_lr_schedule = torch.optim.lr_scheduler.StepLR(\
        goptimizer, 20, gamma=0.5, last_epoch=-1)
d_lr_schedule = torch.optim.lr_scheduler.StepLR(\
        doptimizer, 20, gamma=0.5, last_epoch=-1)
# 用于测试的固定噪声,用来查看相同的潜在张量在训练过程中生成图片的变换
batch_size = 512
fixed_noises = torch.randn(batch_size, latent_size, 1, 1).to(device)
cuda = True if torch.cuda.is_available() else False
Tensor = torch.cuda.FloatTensor if cuda else torch.FloatTensor

# 训练过程
vizx = 0
epoch_num = 8000
for epoch in range(epoch_num):
    for batch in train_loader:
        # 载入本批次数据
        # real_images, _ = data
        rimages, rlabels = batch
        rimages = rimages.to(torch.float32)
        rlabels = rlabels.long()
        batch_size = rimages.size(0)
        # batch_size = 1344

        # 训练鉴别网络
        labels = torch.ones(batch_size) # 真实数据对应标签为1
        preds = dnet(rimages.to(device)) # 对真实数据进行判别
        # print(preds.type(),len(preds))
        preds = preds.reshape(-1)
        # print(preds.type(),len(preds))
        # print(labels.type(),len(labels))
        # print(preds.size(),preds)

        dloss_real = criterion(preds.to(device), labels.to(device)) # 真实数据的鉴别器损失
        dmean_real = preds.sigmoid().mean()
                # 计算鉴别器将多少比例的真数据判定为真,仅用于输出显示

        noises = torch.randn(batch_size, latent_size, 1, 1) # 潜在噪声
        fake_images = gnet(noises.to(device)) # 生成假数据
        labels = torch.zeros(batch_size) # 假数据对应标签为0
        fake = fake_images.detach()
                # 使得梯度的计算不回溯到生成网络,可用于加快训练速度.删去此步结果不变
        preds = dnet(fake) # 对假数据进行鉴别
        preds = preds.view(-1)
        dloss_fake = criterion(preds.to(device), labels.to(device)) # 假数据的鉴别器损失
        dmean_fake = preds.sigmoid().mean()
                # 计算鉴别器将多少比例的假数据判定为真,仅用于输出显示

        dloss = dloss_real + dloss_fake # 总的鉴别器损失
        dnet.zero_grad()
        dloss.backward()
        doptimizer.step()
        # now_dloss += dloss.item()
        # 训练生成网络
        labels = torch.ones(batch_size)
                # 生成网络希望所有生成的数据都被认为是真数据
        preds = dnet(fake_images) # 把假数据通过鉴别网络
        preds = preds.view(-1)
        gloss = criterion(preds.to(device), labels.to(device)) # 真数据看到的损失
        gmean_fake = preds.sigmoid().mean()
                # 计算鉴别器将多少比例的假数据判定为真,仅用于输出显示
        gnet.zero_grad()
        gloss.backward()
        goptimizer.step()
        # now_gloss += gloss.item()
        # 输出本步训练结果
        # print(
        #         "epoch",epoch,
        #         "now_dloss",now_dloss,
        #         "now_gloss",now_gloss,
        #         "correct",dmean_real, dmean_fake, gmean_fake
        # )


        print('[{}/{}]'.format(epoch, epoch_num) +
                '鉴别网络损失:{:g} 生成网络损失:{:g}'.format(dloss, gloss) +
                '真数据判真比例:{:g} 假数据判真比例:{:g}/{:g}'.format(
                dmean_real, dmean_fake, gmean_fake))

        # print('[{}/{}]'.format(epoch, epoch_num) +
        #         '[{}/{}]'.format(batch, len(train_loader)) +
        #         '鉴别网络损失:{:g} 生成网络损失:{:g}'.format(dloss, gloss) +
        #         '真数据判真比例:{:g} 假数据判真比例:{:g}/{:g}'.format(
        #         dmean_real, dmean_fake, gmean_fake))

        # if batch_idx % 100 == 0:
        #     fake = gnet(fixed_noises) # 由固定潜在张量生成假数据
        #     save_image(fake, # 保存假数据
        #             './data/images_epoch{:02d}_batch{:03d}.png'.format(
        #             epoch, batch_idx))
         # 可视化
        vizx+=1
        viz.line([float(gloss)],[vizx],win='G_loss', update='append',opts=dict(title='G_loss'))
        viz1.line([float(dloss)],[vizx],win='D_loss', update='append',opts=dict(title='D_loss'))
        viz2.line([float(doptimizer.state_dict()['param_groups'][0]['lr'])],[vizx],\
            win='D_lr', update='append',opts=dict(title='D_lr'))
        viz3.line([float(goptimizer.state_dict()['param_groups'][0]['lr'])],[vizx],\
            win='G_lr', update='append',opts=dict(title='G_lr'))
        viz4.line([float(dmean_real)],[vizx],\
            win='D real', update='append',opts=dict(title='D real真判真'))
        viz5.line([float(gmean_fake)],[vizx],\
            win='D fake', update='append',opts=dict(title='D fake假判真'))    
        viz6.line([float(gloss)],[epoch],win='G_loss_perEpoch', update='append',opts=dict(title='G_loss_perEpoch'))
        viz7.line([float(dloss)],[epoch],win='D_loss_perEpoch', update='append',opts=dict(title='D_loss_perEpoch'))
        viz8.line([float(doptimizer.state_dict()['param_groups'][0]['lr'])],[epoch],\
            win='D_lr_perEpoch', update='append',opts=dict(title='D_lr_perEpoch'))
        viz9.line([float(goptimizer.state_dict()['param_groups'][0]['lr'])],[epoch],\
            win='G_lr_perEpoch', update='append',opts=dict(title='G_lr_perEpoch'))
        viz10.line([float(dmean_real)],[epoch],\
            win='D real_perEpoch', update='append',opts=dict(title='D real真判真_perEpoch'))
        viz11.line([float(gmean_fake)],[epoch],\
            win='D fake_perEpoch', update='append',opts=dict(title='D fake假判真_perEpoch'))     
    # 更新学习率
    g_lr_schedule.step()
    d_lr_schedule.step()
    
    # 定期保存
    timeForSave = datetime.datetime.now().strftime('%Y_%m_%d_%H_%M_%S')
    checkpointPath_g = ckpDir+'g_ep_'+str(epoch)+'_'+timeForSave+'.pth'
    checkpointPath_d = ckpDir+'d_ep_'+str(epoch)+'_'+timeForSave+'.pth'
    d_state = {'model': dnet.state_dict(), 'optimizer': doptimizer.state_dict(), 'epoch': epoch}
    torch.save(d_state, checkpointPath_d)
    g_state = {'model': gnet.state_dict(), 'optimizer': goptimizer.state_dict(), 'epoch': epoch}
    torch.save(g_state, checkpointPath_g)

torch.save(gnet.state_dict(),'./generator.pth')

torch.save(dnet.state_dict(),'./discriminator.pth')

[0/8000]鉴别网络损失:2.00886 生成网络损失:1.30387真数据判真比例:0.263897 假数据判真比例:0.271559/0.271519
[0/8000]鉴别网络损失:4.30031 生成网络损失:1.54757真数据判真比例:0.0273812 假数据判真比例:0.212847/0.212823
[0/8000]鉴别网络损失:2.67895 生成网络损失:1.34729真数据判真比例:0.114807 假数据判真比例:0.260011/0.259986
[0/8000]鉴别网络损失:4.45626 生成网络损失:1.28953真数据判真比例:0.0253422 假数据判真比例:0.275496/0.275466
[0/8000]鉴别网络损失:3.35821 生成网络损失:1.25149真数据判真比例:0.108245 假数据判真比例:0.286152/0.286121
[0/8000]鉴别网络损失:3.62148 生成网络损失:1.22555真数据判真比例:0.0688117 假数据判真比例:0.29368/0.293645
[0/8000]鉴别网络损失:3.91492 生成网络损失:1.19342真数据判真比例:0.0601027 假数据判真比例:0.303273/0.303234
[0/8000]鉴别网络损失:3.29915 生成网络损失:1.18131真数据判真比例:0.0884157 假数据判真比例:0.30698/0.306937
[0/8000]鉴别网络损失:2.7341 生成网络损失:1.18273真数据判真比例:0.114415 假数据判真比例:0.306535/0.306493
[0/8000]鉴别网络损失:0.382306 生成网络损失:1.17548真数据判真比例:0.987151 假数据判真比例:0.308787/0.308724
[0/8000]鉴别网络损失:2.26445 生成网络损失:1.16815真数据判真比例:0.168073 假数据判真比例:0.311035/0.310984
[0/8000]鉴别网络损失:3.53347 生成网络损失:1.16037真数据判真比例:0.0498964 假数据判真比例:0.313488/0.313441
[0/8000]鉴别网络损失:2.54241 生成网络损失:1.1659

KeyboardInterrupt: 

In [ ]:
# import torch
# torch.cuda.is_available()
# device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
# print(device)

In [ ]:
# import torch
# print(torch.version.cuda)